In [1]:
import tensorflow as tf
import os
from keras.layers import (Input, Dense, Flatten, Conv2D, MaxPooling2D, Dropout)
from keras.models import Model, load_model
from keras.optimizers import Adam
from keras.preprocessing.image import ImageDataGenerator
from keras.callbacks import TensorBoard
import time

In [8]:
datapath = '../spectrograms3sec'
genres = list(os.listdir(f'{datapath}/train/'))
genres.remove('.DS_Store')
print(genres)

['pop', 'metal', 'disco', 'blues', 'reggae', 'classical', 'rock', 'hiphop', 'country', 'jazz']


In [9]:
#Data has been pre split into test and training folders

data_gen=tf.keras.preprocessing.image.ImageDataGenerator(rescale=1./255.)
path=f'{datapath}/train' 
image_datagentrain=data_gen.flow_from_directory(path,target_size=(300,300),class_mode='categorical')

Found 8990 images belonging to 10 classes.


In [10]:
path=f'{datapath}/test'
image_datagentest=data_gen.flow_from_directory(path,target_size=(300,300),class_mode='categorical')

Found 1000 images belonging to 10 classes.


In [28]:
def GenreModel(input_shape=(300,300,4), classes=10, model_name='3sec_GenreModel_'):
    
    model_name=model_name + str(int(time.time()))[4:]
    tensorboard = TensorBoard(log_dir=f'logs/{model_name}')

    X_input = Input(input_shape)
    
    X = (Conv2D(filters=8, kernel_size=(3,3), padding='same', activation='relu', input_shape=(300, 300, 3)))(X_input)
    X = (MaxPooling2D(pool_size=(2,2), strides=(2,2)))(X)

    X = (Conv2D(filters=16, kernel_size=(3,3), padding='same', activation='relu',))(X)
    X = (MaxPooling2D(pool_size=(2,2), strides=(2,2)))(X)

    X = (Conv2D(filters=32, kernel_size=(3,3), padding='same', activation='relu',))(X)
    X = (MaxPooling2D(pool_size=(2,2), strides=(2,2)))(X)

    X = (Conv2D(filters=64, kernel_size=(3,3), padding='same', activation='relu',))(X)
    X = (MaxPooling2D(pool_size=(2,2), strides=(2,2)))(X)

    X = Flatten()(X)

    X = Dropout(rate=0.3)(X)

    X = (Dense(128, activation='relu'))(X)
    X = (Dense(64, activation='relu'))(X)
    X = (Dense(10, activation='softmax'))(X)

    model = Model(X_input,X)
    
    return model, tensorboard

model, tensorboard = GenreModel(input_shape=(300,300,3),classes=10)

model.compile(loss='categorical_crossentropy', optimizer=Adam(learning_rate=0.0005), metrics=['accuracy'])

history = model.fit(image_datagentrain,
                    epochs=25,
                    callbacks = [tensorboard],
                    batch_size=32,
                    validation_data=image_datagentest).history

Epoch 1/25
281/281 [==============================] - 150s 535ms/step - loss: 1.8046 - accuracy: 0.3341 - val_loss: 1.3784 - val_accuracy: 0.5140
Epoch 2/25
281/281 [==============================] - 154s 547ms/step - loss: 1.2577 - accuracy: 0.5496 - val_loss: 1.1384 - val_accuracy: 0.6250
Epoch 3/25
281/281 [==============================] - 154s 548ms/step - loss: 1.0491 - accuracy: 0.6290 - val_loss: 1.0024 - val_accuracy: 0.6600
Epoch 4/25
281/281 [==============================] - 151s 537ms/step - loss: 0.9201 - accuracy: 0.6804 - val_loss: 0.9822 - val_accuracy: 0.6570
Epoch 5/25
281/281 [==============================] - 150s 534ms/step - loss: 0.8171 - accuracy: 0.7171 - val_loss: 0.8176 - val_accuracy: 0.7270
Epoch 6/25
281/281 [==============================] - 150s 535ms/step - loss: 0.7101 - accuracy: 0.7521 - val_loss: 0.7503 - val_accuracy: 0.7400
Epoch 7/25
281/281 [==============================] - 151s 538ms/step - loss: 0.6408 - accuracy: 0.7796 - val_loss: 0.7216 -

In [12]:
loss, accuracy = model.evaluate(image_datagentest)
print('loss: ', loss, 'accuracy: ', accuracy)

32/32 [==============================] - 5s 158ms/step - loss: 0.8352 - accuracy: 0.7960
loss:  0.8352094888687134 accuracy:  0.7960000038146973


### TensorBoard
We can view an overview of our results in tensorboard.

In [100]:
from tensorboard import notebook

%reload_ext tensorboard
# Command line in current working dir "tensorboard --logdir='logs/'" to start tensorboard
%tensorboard --logdir {'logs/'}

## Optimizing Model structure
Now that we have a basic model that works using hyperas we will find the optimal number of layers and layer sizes for the model, using tensorboard to visualise the results. It is possible that the current model is already optimal. To ealuate the models performance we will use the validation loss parameter. The hyperas library uses hyperopt, and allows us to feed the model a range fo possible parameters such as number of layers and number of nodes per layer.

In [14]:
import hyperas
from hyperas import optim
from hyperas.distributions import choice
from hyperopt import tpe, STATUS_OK, Trials
from keras.utils import np_utils

In [18]:
def GenreModel_optimize(X_train, Y_train, X_test, Y_test):

    X_input = Input((300,300,3))
    
    X = (Conv2D({{choice([8,16])}}, kernel_size=(3,3), padding='same', activation='relu', input_shape=(300, 300, 3)))(X_input)
    X = (MaxPooling2D(pool_size=(2,2), strides=(2,2)))(X)

    X = (Conv2D({{choice([8,16,32])}}, kernel_size=(3,3), padding='same', activation='relu',))(X)
    X = (MaxPooling2D(pool_size=(2,2), strides=(2,2)))(X)

    X = (Conv2D({{choice([16,32,64])}}, kernel_size=(3,3), padding='same', activation='relu',))(X)
    X = (MaxPooling2D(pool_size=(2,2), strides=(2,2)))(X)
    
    X = (Conv2D({{choice([32,64,128])}}, kernel_size=(3,3), padding='same', activation='relu',))(X)
    X = (MaxPooling2D(pool_size=(2,2), strides=(2,2)))(X)
    
    nb_conv = {{choice(['four','five'])}}
    if nb_conv == 'five':
        X = (Conv2D({{choice([64,128,256])}}, kernel_size=(3,3), padding='same', activation='relu',))(X)
        X = (MaxPooling2D(pool_size=(2,2), strides=(2,2)))(X)

    X = Flatten()(X)

    X = Dropout(rate=0.3)(X)
    
    nb_dense = {{choice(['one','two','three'])}}
    X = (Dense({{choice([64,128,256,512])}}, activation='relu'))(X)
    if nb_dense == 'two' or 'three':
        X = (Dense({{choice([32,64,128,256])}}, activation='relu'))(X)
        if nb_dense == 'three':
            X = (Dense({{choice([32,64,128,256])}}, activation='relu'))(X)

    
    X = (Dense(10, activation='softmax'))(X)

    model = Model(X_input,X)
    
    model.compile(loss='categorical_crossentropy',
                 optimizer=Adam(learning_rate=0.0005),
                 metrics=['accuracy'])
    
    batch_size = {{choice([32,64,128])}}
    history = model.fit(X_train,
                        epochs=20,
                        batch_size=batch_size,
                        validation_data=X_test).history
    
    
    
    return {'loss' : history['val_loss'][-1], 'status' : STATUS_OK, 'model' : model}

Hyperas requires a data function to feed to the `optim.minimize` funciton.

In [19]:
def data():
    nb_classes = 10
    
    data_gen=ImageDataGenerator(rescale=1./255.)

    X_train = data_gen.flow_from_directory('../spectrograms3sec/train',target_size=(300,300),class_mode='categorical')
    X_test = data_gen.flow_from_directory('../spectrograms3sec/test',target_size=(300,300),class_mode='categorical')
    
    y_train = X_train.classes
    y_test = X_test.classes
    
    Y_train = np_utils.to_categorical(y_train, nb_classes)
    Y_test = np_utils.to_categorical(y_test, nb_classes)
    return X_train, Y_train, X_test, Y_test


We optimize the model using the optim function from hyperas.

In [33]:
X_train, Y_train, X_test, Y_test = data()

trials=Trials()

best_run, best_model = optim.minimize(model=GenreModel_optimize,
                                          data=data,
                                          max_evals=5,
                                          algo=tpe.suggest,
                                          notebook_name='CNNFinal',
                                          trials=trials)

print(best_model)

Found 8990 images belonging to 10 classes.
Found 1000 images belonging to 10 classes.
>>> Imports:
#coding=utf-8

try:
    import tensorflow as tf
except:
    pass

try:
    import os
except:
    pass

try:
    from keras.layers import Input, Dense, Flatten, Conv2D, MaxPooling2D, Dropout
except:
    pass

try:
    from keras.models import Model, load_model
except:
    pass

try:
    from keras.optimizers import Adam
except:
    pass

try:
    from keras.preprocessing.image import ImageDataGenerator
except:
    pass

try:
    from keras.callbacks import TensorBoard
except:
    pass

try:
    import time
except:
    pass

try:
    from tensorboard import notebook
except:
    pass

try:
    import hyperas
except:
    pass

try:
    from hyperas import optim
except:
    pass

try:
    from hyperas.distributions import choice
except:
    pass

try:
    from hyperopt import tpe, STATUS_OK, Trials
except:
    pass

try:
    from keras.utils import np_utils
except:
    pass

>>> Hyperas search

                                                    
 24/281 [=>............................]             
 - ETA: 2:47 - loss: 2.3064 - accuracy: 0.1146       
                                                    
 25/281 [=>............................]             
 - ETA: 2:47 - loss: 2.3068 - accuracy: 0.1112       
                                                    
 26/281 [=>............................]             
 - ETA: 2:47 - loss: 2.3066 - accuracy: 0.1118       
                                                    
 27/281 [=>............................]             
 - ETA: 2:47 - loss: 2.3068 - accuracy: 0.1088       
                                                    
 28/281 [=>............................]             
 - ETA: 2:46 - loss: 2.3065 - accuracy: 0.1116       
                                                    
 29/281 [==>...........................]             
 - ETA: 2:46 - loss: 2.3062 - accuracy: 0.1121       
                                  

 - ETA: 2:22 - loss: 2.2867 - accuracy: 0.1339       
                                                    
 75/281 [=======>......................]             
 - ETA: 2:21 - loss: 2.2861 - accuracy: 0.1329       
                                                    
 76/281 [=======>......................]             
 - ETA: 2:21 - loss: 2.2864 - accuracy: 0.1328       
                                                    
 77/281 [=======>......................]             
 - ETA: 2:20 - loss: 2.2873 - accuracy: 0.1327       
                                                    
 78/281 [=======>......................]             
 - ETA: 2:19 - loss: 2.2859 - accuracy: 0.1346       
                                                    
 79/281 [=======>......................]             
 - ETA: 2:19 - loss: 2.2848 - accuracy: 0.1353       
                                                    
 80/281 [=======>......................]             
 - ETA: 2:18 - loss: 2.2844 - accu

125/281 [============>.................]             
 - ETA: 1:48 - loss: 2.2058 - accuracy: 0.1748       
                                                    
126/281 [============>.................]             
 - ETA: 1:48 - loss: 2.2043 - accuracy: 0.1751       
                                                    
127/281 [============>.................]             
 - ETA: 1:47 - loss: 2.2032 - accuracy: 0.1757       
                                                    
128/281 [============>.................]             
 - ETA: 1:46 - loss: 2.1994 - accuracy: 0.1765       
                                                    
129/281 [============>.................]             
 - ETA: 1:46 - loss: 2.1972 - accuracy: 0.1778       
                                                    
130/281 [============>.................]             
 - ETA: 1:45 - loss: 2.1963 - accuracy: 0.1781       
                                                    
131/281 [============>............

                                                    
176/281 [=================>............]             
 - ETA: 1:14 - loss: 2.0900 - accuracy: 0.2173       
                                                    
177/281 [=================>............]             
 - ETA: 1:13 - loss: 2.0863 - accuracy: 0.2188       
                                                    
178/281 [==================>...........]             
 - ETA: 1:12 - loss: 2.0850 - accuracy: 0.2200       
                                                    
179/281 [==================>...........]             
 - ETA: 1:11 - loss: 2.0829 - accuracy: 0.2203       
                                                    
180/281 [==================>...........]             
 - ETA: 1:11 - loss: 2.0821 - accuracy: 0.2208       
                                                    
181/281 [==================>...........]             
 - ETA: 1:10 - loss: 2.0804 - accuracy: 0.2212       
                                  

...

 - ETA: 2:07 - loss: 0.0544 - accuracy: 0.9819                                      
                                                                                   
136/281 [=============>................]                                            
 - ETA: 2:06 - loss: 0.0542 - accuracy: 0.9821                                      
                                                                                   
137/281 [=============>................]                                            
 - ETA: 2:05 - loss: 0.0545 - accuracy: 0.9818                                      
                                                                                   
138/281 [=============>................]                                            
 - ETA: 2:04 - loss: 0.0543 - accuracy: 0.9817                                      
                                                                                   
139/281 [=============>................]                             

 - ETA: 1:38 - loss: 0.0622 - accuracy: 0.9779                                      
                                                                                   
168/281 [================>.............]                                            
 - ETA: 1:37 - loss: 0.0632 - accuracy: 0.9779                                      
                                                                                   
169/281 [=================>............]                                            
 - ETA: 1:37 - loss: 0.0633 - accuracy: 0.9778                                      
                                                                                   
170/281 [=================>............]                                            
 - ETA: 1:36 - loss: 0.0637 - accuracy: 0.9776                                      
                                                                                   
171/281 [=================>............]                             

 - ETA: 1:10 - loss: 0.0673 - accuracy: 0.9769                                      
                                                                                   
200/281 [====================>.........]                                            
 - ETA: 1:09 - loss: 0.0671 - accuracy: 0.9770                                      
                                                                                   
201/281 [====================>.........]                                            
 - ETA: 1:08 - loss: 0.0674 - accuracy: 0.9768                                      
                                                                                   
202/281 [====================>.........]                                            
 - ETA: 1:08 - loss: 0.0676 - accuracy: 0.9768                                      
                                                                                   
203/281 [====================>.........]                             

 - ETA: 42s - loss: 0.0720 - accuracy: 0.9748                                       
                                                                                    
232/281 [=======================>......]                                            
 - ETA: 41s - loss: 0.0726 - accuracy: 0.9745                                       
                                                                                    
233/281 [=======================>......]                                            
 - ETA: 41s - loss: 0.0735 - accuracy: 0.9742                                       
                                                                                    
234/281 [=======================>......]                                            
 - ETA: 40s - loss: 0.0743 - accuracy: 0.9740                                       
                                                                                    
235/281 [========================>.....]                         

 - ETA: 15s - loss: 0.0804 - accuracy: 0.9717                                       
                                                                                    
264/281 [===========================>..]                                            
 - ETA: 14s - loss: 0.0806 - accuracy: 0.9716                                       
                                                                                    
265/281 [===========================>..]                                            
 - ETA: 13s - loss: 0.0808 - accuracy: 0.9715                                       
                                                                                    
266/281 [===========================>..]                                            
 - ETA: 12s - loss: 0.0812 - accuracy: 0.9712                                       
                                                                                    
267/281 [===========================>..]                         

We see the results of the optimization by looking at the best run.

In [34]:
# 'Conv2D': hp.choice('Conv2D', [8,16]),
# 'Conv2D_1': hp.choice('Conv2D_1', [8,16,32]),
# 'Conv2D_2': hp.choice('Conv2D_2', [16,32,64]),
# 'Conv2D_3': hp.choice('Conv2D_3', [32,64,128]),
# 'nb_conv': hp.choice('nb_conv', ['four','five']),
# 'Conv2D_4': hp.choice('Conv2D_4', [64,128,256]),
# 'nb_dense': hp.choice('nb_dense', ['one','two','three']),
# 'Dense': hp.choice('Dense', [64,128,256,512]),
# 'Dense_1': hp.choice('Dense_1', [32,64,128,256]),
# 'Dense_2': hp.choice('Dense_2', [32,64,128,256]),
# 'batch_size': hp.choice('batch_size', [32,64,128]), (called Conv2D_5 in output)
best_run

{'Conv2D': 1,
 'Conv2D_1': 0,
 'Conv2D_2': 2,
 'Conv2D_3': 2,
 'Conv2D_4': 1,
 'Conv2D_5': 2,
 'Dense': 3,
 'Dense_1': 3,
 'Dense_2': 2,
 'nb_conv': 1,
 'nb_dense': 0}

In [42]:
best_model.summary()

Model: "functional_19"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_10 (InputLayer)        [(None, 300, 300, 3)]     0         
_________________________________________________________________
conv2d_41 (Conv2D)           (None, 300, 300, 16)      448       
_________________________________________________________________
max_pooling2d_41 (MaxPooling (None, 150, 150, 16)      0         
_________________________________________________________________
conv2d_42 (Conv2D)           (None, 150, 150, 8)       1160      
_________________________________________________________________
max_pooling2d_42 (MaxPooling (None, 75, 75, 8)         0         
_________________________________________________________________
conv2d_43 (Conv2D)           (None, 75, 75, 64)        4672      
_________________________________________________________________
max_pooling2d_43 (MaxPooling (None, 37, 37, 64)      

In [50]:
# def train_best_model(best_model, name='Optimized_model_'):
#     model_name = name + str(int(time.time()))[4:]
#     tensorboard = TensorBoard(log_dir=f'logs/{model_name}')
    
#     best_model.compile(loss='categorical_crossentropy',
#                       optimizer=Adam(learning_rate=0.0005),
#                       metrics=['accuracy'])
    
#     history = best_model.fit(image_datagentrain,
#                             epochs=25,
#                             batch_size=128,
#                             validation_data=image_datagentest)
#     return history

In [ ]:
# previous best_run loss 0.5
# {'Conv2D': 0,
#  'Conv2D_1': 2,
#  'Conv2D_2': 2,
#  'Conv2D_3': 1,
#  'Conv2D_4': 1,
#  'Conv2D_5': 1,
#  'Dense': 3,
#  'Dense_1': 2,
#  'Dense_2': 0,
#  'nb_conv': 1,
#  'nb_dense': 2}

In [54]:
def GenreModel(input_shape=(300,300,4), classes=10, model_name='opto_GenreModel_'):
    
    model_name=model_name + str(int(time.time()))[4:]
    tensorboard = TensorBoard(log_dir=f'logs/{model_name}')

    X_input = Input(input_shape)
    
    X = (Conv2D(filters=8, kernel_size=(3,3), padding='same', activation='relu', input_shape=(300, 300, 3)))(X_input)
    X = (MaxPooling2D(pool_size=(2,2), strides=(2,2)))(X)

    X = (Conv2D(filters=16, kernel_size=(3,3), padding='same', activation='relu',))(X)
    X = (MaxPooling2D(pool_size=(2,2), strides=(2,2)))(X)

    X = (Conv2D(filters=64, kernel_size=(3,3), padding='same', activation='relu',))(X)
    X = (MaxPooling2D(pool_size=(2,2), strides=(2,2)))(X)

    X = (Conv2D(filters=128, kernel_size=(3,3), padding='same', activation='relu',))(X)
    X = (MaxPooling2D(pool_size=(2,2), strides=(2,2)))(X)
    
    X = (Conv2D(filters=128, kernel_size=(3,3), padding='same', activation='relu',))(X)
    X = (MaxPooling2D(pool_size=(2,2), strides=(2,2)))(X)

    X = Flatten()(X)

    X = Dropout(rate=0.3)(X)

    X = (Dense(512, activation='relu'))(X)
    X = (Dense(256, activation='relu'))(X)
    X = (Dense(10, activation='softmax'))(X)

    model = Model(X_input,X)
    
    return model, tensorboard

model, tensorboard = GenreModel(input_shape=(300,300,3),classes=10)

model.compile(loss='categorical_crossentropy', optimizer=Adam(learning_rate=0.0005), metrics=['accuracy'])

history = model.fit(image_datagentrain,
                    epochs=25,
                    callbacks = [tensorboard],
                    batch_size=128,
                    validation_data=image_datagentest).history

Epoch 1/25
281/281 [==============================] - 198s 705ms/step - loss: 1.8427 - accuracy: 0.3122 - val_loss: 1.4225 - val_accuracy: 0.4910
Epoch 2/25
281/281 [==============================] - 198s 704ms/step - loss: 1.3179 - accuracy: 0.5180 - val_loss: 1.1308 - val_accuracy: 0.6200
Epoch 3/25
281/281 [==============================] - 199s 707ms/step - loss: 1.0563 - accuracy: 0.6236 - val_loss: 0.9922 - val_accuracy: 0.6520
Epoch 4/25
281/281 [==============================] - 197s 702ms/step - loss: 0.9118 - accuracy: 0.6731 - val_loss: 0.8781 - val_accuracy: 0.7070
Epoch 5/25
281/281 [==============================] - 200s 713ms/step - loss: 0.7977 - accuracy: 0.7215 - val_loss: 0.8084 - val_accuracy: 0.7220
Epoch 6/25
281/281 [==============================] - 210s 746ms/step - loss: 0.6954 - accuracy: 0.7587 - val_loss: 0.7031 - val_accuracy: 0.7630
Epoch 7/25
281/281 [==============================] - 213s 759ms/step - loss: 0.6176 - accuracy: 0.7811 - val_loss: 0.6867 -

In [62]:
from keras.models import model_from_json

model_json = model.to_json()
with open("model2.json", "w") as json_file:
    json_file.write(model_json)
# serialize weights to HDF5
model.save_weights("model2.h5")
print("Saved model to disk")

Saved model to disk


In [81]:
model.save('json_model')

Instructions for updating:
This property should not be used in TensorFlow 2.0, as updates are applied automatically.
Instructions for updating:
This property should not be used in TensorFlow 2.0, as updates are applied automatically.
INFO:tensorflow:Assets written to: json_model/assets


In [56]:
newdatapath = '../spectrograms3secXX'
genres = list(os.listdir(f'{newdatapath}/train/'))
genres.remove('.DS_Store')
print(genres)

['pop', 'metal', 'disco', 'blues', 'reggae', 'classical', 'rock', 'hiphop', 'country', 'jazz']


In [63]:
#Data has been pre split into test and training folders

data_gen=tf.keras.preprocessing.image.ImageDataGenerator(rescale=1./255.)
path=f'{newdatapath}/train' 
image_datagentrain2=data_gen.flow_from_directory(path,target_size=(128,130),class_mode='categorical')

Found 8992 images belonging to 10 classes.


In [64]:
path=f'{newdatapath}/test'
image_datagentest2=data_gen.flow_from_directory(path,target_size=(128,130),class_mode='categorical')

Found 999 images belonging to 10 classes.


In [65]:
def GenreModel(input_shape=(128,130,3), classes=10, model_name='fast_GenreModel_'):
    
    model_name=model_name + str(int(time.time()))[4:]
    tensorboard = TensorBoard(log_dir=f'logs/{model_name}')

    X_input = Input(input_shape)
    
    X = (Conv2D(filters=8, kernel_size=(3,3), padding='same', activation='relu', input_shape=(128, 130, 3)))(X_input)
    X = (MaxPooling2D(pool_size=(2,2), strides=(2,2)))(X)

    X = (Conv2D(filters=16, kernel_size=(3,3), padding='same', activation='relu',))(X)
    X = (MaxPooling2D(pool_size=(2,2), strides=(2,2)))(X)

    X = (Conv2D(filters=64, kernel_size=(3,3), padding='same', activation='relu',))(X)
    X = (MaxPooling2D(pool_size=(2,2), strides=(2,2)))(X)

    X = (Conv2D(filters=128, kernel_size=(3,3), padding='same', activation='relu',))(X)
    X = (MaxPooling2D(pool_size=(2,2), strides=(2,2)))(X)
    
    X = (Conv2D(filters=128, kernel_size=(3,3), padding='same', activation='relu',))(X)
    X = (MaxPooling2D(pool_size=(2,2), strides=(2,2)))(X)

    X = Flatten()(X)

    X = Dropout(rate=0.3)(X)

    X = (Dense(512, activation='relu'))(X)
    X = (Dense(256, activation='relu'))(X)
    X = (Dense(10, activation='softmax'))(X)

    model = Model(X_input,X)
    
    return model, tensorboard

model2, tensorboard = GenreModel(input_shape=(128,130,3),classes=10)

model2.compile(loss='categorical_crossentropy', optimizer=Adam(learning_rate=0.0005), metrics=['accuracy'])

history = model2.fit(image_datagentrain2,
                    epochs=25,
                    callbacks = [tensorboard],
                    batch_size=128,
                    validation_data=image_datagentest2).history

Epoch 1/25
281/281 [==============================] - 64s 229ms/step - loss: 1.8325 - accuracy: 0.3113 - val_loss: 1.4190 - val_accuracy: 0.4895
Epoch 2/25
281/281 [==============================] - 54s 191ms/step - loss: 1.2697 - accuracy: 0.5338 - val_loss: 1.1894 - val_accuracy: 0.5506
Epoch 3/25
281/281 [==============================] - 51s 181ms/step - loss: 1.0784 - accuracy: 0.6064 - val_loss: 0.9932 - val_accuracy: 0.6446
Epoch 4/25
281/281 [==============================] - 51s 183ms/step - loss: 0.9348 - accuracy: 0.6649 - val_loss: 0.8852 - val_accuracy: 0.6777
Epoch 5/25
281/281 [==============================] - 53s 187ms/step - loss: 0.8406 - accuracy: 0.7052 - val_loss: 0.7621 - val_accuracy: 0.7247
Epoch 6/25
281/281 [==============================] - 50s 178ms/step - loss: 0.7228 - accuracy: 0.7440 - val_loss: 0.7208 - val_accuracy: 0.7568
Epoch 7/25
281/281 [==============================] - 49s 174ms/step - loss: 0.6404 - accuracy: 0.7708 - val_loss: 0.6720 - val_ac

In [77]:
predictions = model.predict(image_datagentest)
predictions

array([[9.8245117e-08, 1.2094360e-15, 5.8764034e-09, ..., 5.1801924e-17,
        7.7073842e-10, 7.3787493e-07],
       [2.6361258e-07, 2.0047415e-09, 4.0824229e-06, ..., 9.3176700e-10,
        6.6286914e-09, 9.9345571e-01],
       [1.6083108e-17, 1.0440877e-24, 1.3416662e-20, ..., 4.1683137e-18,
        2.5611864e-17, 1.5974038e-08],
       ...,
       [7.3542981e-17, 5.3958561e-12, 2.1771760e-09, ..., 9.9975294e-01,
        5.2639748e-06, 5.4423146e-09],
       [3.2831409e-12, 4.2400148e-15, 1.9485756e-12, ..., 1.9539381e-09,
        1.7634368e-02, 1.3820993e-06],
       [1.3118604e-11, 8.1123983e-07, 4.5829464e-02, ..., 6.7314667e-01,
        2.8099358e-01, 2.0019193e-05]], dtype=float32)

In [74]:
import numpy as np
genres[np.argmax(predictions[89])]

'blues'

In [80]:
for i in range(len(predictions)):
    print(np.argmax(predictions[i]))

3
9
6
4
6
3
7
3
3
6
7
2
9
2
3
2
9
8
3
5
3
0
5
0
9
0
1
2
6
4
8
4
1
2
7
3
4
1
8
5
0
7
1
5
8
9
0
7
0
0
0
6
4
4
2
1
2
7
5
1
1
5
9
9
3
8
9
7
2
8
0
1
9
7
8
7
3
2
6
0
3
5
6
0
8
7
9
7
3
8
3
1
9
7
0
3
7
2
2
2
6
6
6
4
8
2
2
3
6
4
9
8
0
2
1
6
4
8
6
6
3
4
7
1
4
5
8
6
7
0
2
6
7
4
0
9
6
4
3
8
4
0
6
9
7
8
2
0
4
1
6
8
7
3
7
2
4
5
8
7
7
2
9
2
2
2
5
8
8
0
2
3
0
7
2
4
7
2
0
1
7
7
9
3
8
1
5
3
4
7
0
8
6
8
3
9
1
5
9
5
3
6
1
4
5
6
0
5
1
7
5
9
2
2
3
9
3
5
5
7
4
0
7
4
1
9
6
1
2
7
9
5
5
8
5
8
6
5
2
4
9
8
7
6
8
7
1
0
1
8
3
7
1
4
7
7
3
3
6
2
1
9
9
6
1
3
9
8
5
9
3
6
5
7
9
0
2
1
9
4
0
1
0
4
3
3
8
0
0
8
7
5
0
9
3
4
5
9
2
5
2
1
3
6
7
3
8
9
4
5
3
9
7
4
1
3
1
4
0
8
6
5
9
4
5
1
9
1
1
1
4
0
1
0
2
0
7
6
1
0
9
0
9
0
8
2
1
6
9
2
6
8
8
6
1
5
0
8
0
0
9
2
1
1
0
8
0
0
6
4
3
5
5
8
3
3
7
9
6
8
9
7
0
7
0
5
8
0
8
2
8
1
9
6
0
9
7
9
1
2
0
5
3
0
3
1
1
7
3
2
3
4
9
6
1
9
2
1
8
0
6
8
8
9
0
4
8
9
9
1
0
3
2
6
8
5
2
9
9
7
9
3
4
4
5
7
5
5
6
7
5
2
8
6
2
0
2
2
3
6
6
6
5
8
9
2
1
7
2
5
0
4
5
0
1
6
2
8
9
9
0
9
9
0
6
3
4
5
3
4
3
8
9
2
3
0
7
1
4
7


In [99]:
from keras.utils import plot_model
import pydot
plot_model(model2, to_file='model_test.png')

('Failed to import pydot. You must `pip install pydot` and install graphviz (https://graphviz.gitlab.io/download/), ', 'for `pydotprint` to work.')


In [93]:
pip install pydot


  Using cached pydot-1.4.2-py2.py3-none-any.whl (21 kB)
Note: you may need to restart the kernel to use updated packages.


In [94]:
pip install pydotplus

     |████████████████████████████████| 278 kB 3.9 MB/s eta 0:00:01
  Created wheel for pydotplus: filename=pydotplus-2.0.2-py3-none-any.whl size=24566 sha256=c902caa1ade81a4a22a328208e0298b6f1b6cdff1ac9c6aae3cd89dd7a139101
  Stored in directory: /Users/jayvier/Library/Caches/pip/wheels/fe/cd/78/a7e873cc049759194f8271f780640cf96b35e5a48bef0e2f36
Successfully built pydotplus
Note: you may need to restart the kernel to use updated packages.


In [96]:
pip install graphviz

Note: you may need to restart the kernel to use updated packages.
